<a href="https://colab.research.google.com/github/AshishGusain17/Grad-CAM-implementation/blob/master/tf-explain-untrained.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
%matplotlib inline
import pandas as pd
import os,shutil,math,scipy,cv2
import numpy as np
import matplotlib.pyplot as plt
import random as rn
import seaborn as sn


from sklearn.utils import shuffle
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import confusion_matrix,roc_curve,auc

from PIL import Image
from PIL import Image as pil_image
from PIL import ImageDraw

from time import time
from glob import glob
from tqdm import tqdm
from skimage.io import imread
from IPython.display import SVG

from scipy import misc,ndimage
from scipy.ndimage.interpolation import zoom
# from scipy.ndimage import imread

import keras
import tensorflow as tf
from keras import backend as K
from keras.utils.np_utils import to_categorical
from keras import layers
from keras.preprocessing.image import save_img
from keras.utils.vis_utils import model_to_dot
from keras.applications.vgg16 import VGG16,preprocess_input
from keras.models import Sequential,Input,Model
from keras.layers import Dense,Flatten,Dropout,Concatenate,GlobalAveragePooling2D,Lambda,ZeroPadding2D
from keras.layers import SeparableConv2D,BatchNormalization,MaxPooling2D,Conv2D
from keras import regularizers
from keras.preprocessing.image import ImageDataGenerator
from keras.optimizers import Adam,SGD
from keras.utils.vis_utils import plot_model
from keras.callbacks import ModelCheckpoint,EarlyStopping,TensorBoard,CSVLogger,ReduceLROnPlateau,LearningRateScheduler
import tf_explain


In [3]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
def show_final_history(history):
    fig, ax = plt.subplots(1, 2, figsize=(15,5))
    ax[0].set_title('loss')
    ax[0].plot(history.epoch, history.history["loss"], label="Training loss")
    ax[0].plot(history.epoch, history.history["val_loss"], label="Validation loss")
    ax[1].set_title('acc')
    ax[1].plot(history.epoch, history.history["accuracy"], label="Training accuracy")
    ax[1].plot(history.epoch, history.history["val_accuracy"], label="Validation accuracy")
    ax[0].legend()
    # ax[1].legend()


In [88]:
import h5py
data = h5py.File('/content/drive/My Drive/danceForms/train_224.h5', "r")
print(np.array(data))
XX = data["X"][:]
ZZ = data["Z"][:]

num = XX.shape[0] 
print(XX.shape,ZZ.shape,num)

['X' 'Z']
(364, 224, 224, 3) (364,) 364


In [89]:
x_train,x_test,y_train,y_test = train_test_split(XX,ZZ,test_size=0.2,random_state=42)



y_train = to_categorical(y_train,8)
x_train = x_train/255
print(x_train.shape,y_train.shape)
print(x_test.shape,y_test.shape)

(291, 224, 224, 3) (291, 8)
(73, 224, 224, 3) (73,)


In [0]:
augs_gen = ImageDataGenerator(
            zoom_range=0.2, 
            rotation_range=10,
            width_shift_range=0.3, 
            height_shift_range=0.3,
             shear_range=0.4,
             horizontal_flip=True,
              fill_mode='nearest',
             
        featurewise_center=False,  
        samplewise_center=False, 
        featurewise_std_normalization=False,  
        samplewise_std_normalization=False,  
        zca_whitening=False,  
        # rotation_range=20,  
        # zoom_range = 0.1, 
        # width_shift_range=0.2,  
        # height_shift_range=0.2, 
        # horizontal_flip=True,  
        ) 

augs_gen.fit(x_train)

In [0]:
# fig,ax=plt.subplots(5,5)
# fig.set_size_inches(15,15)
# print(len(Z))
# for i in range(5):
#     for j in range (5):
#         l=rn.randint(0,len(Z))
#         ax[i,j].imshow(XX[l])
#         ax[i,j].set_title('Category: '+ str(l))
        
# plt.tight_layout()

In [121]:
ct=0
imgsize = 224
base_model = tf.keras.applications.ResNet50(include_top=False,
                  input_shape = (imgsize,imgsize,3),
                  weights = 'imagenet')
base_model.summary()

model =  tf.keras.models.Sequential()
model.add(base_model)
for layer in base_model.layers:
  ct=ct+1

for layer in base_model.layers:
  if ct>10:
    layer.trainable = False
  else:
    layer.trainable = True
  ct=ct-1
  print(layer,layer.trainable)

model.add(tf.keras.layers.Conv2D(filters=512, kernel_size=(3, 3), activation='relu' , name="explain_layer"))
model.add(tf.keras.layers.Flatten())
# model.add(tf.keras.layers.Dropout(0.5))
# model.add(tf.keras.layers.Dense(1024,activation='relu'))
model.add(tf.keras.layers.Dropout(0.5))
model.add(tf.keras.layers.Dense(512,activation='relu' ))
model.add(tf.keras.layers.Dense(8, activation='softmax'))
model.summary()

# SVG(tf.keras.utils.vis_utils.model_to_dot(model).create(prog='dot', format='svg'))
# plot_model(model, to_file='model_plot.png', show_shapes=True, show_layer_names=True)

Model: "resnet50"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_23 (InputLayer)           [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
conv1_pad (ZeroPadding2D)       (None, 230, 230, 3)  0           input_23[0][0]                   
__________________________________________________________________________________________________
conv1_conv (Conv2D)             (None, 112, 112, 64) 9472        conv1_pad[0][0]                  
__________________________________________________________________________________________________
conv1_bn (BatchNormalization)   (None, 112, 112, 64) 256         conv1_conv[0][0]                 
___________________________________________________________________________________________

In [0]:
# def create_model(input_shape=(224, 224, 3), num_classes=8):
#     img_input = tf.keras.Input(input_shape)

#     x = tf.keras.layers.Conv2D(filters=32, kernel_size=(3, 3), activation='relu')(img_input)
#     x = tf.keras.layers.Conv2D(filters=64, kernel_size=(3, 3), activation='relu', name='target12')(x)
#     print(x.shape)
#     x = tf.keras.layers.MaxPool2D(pool_size=(2, 2))(x)

#     x = tf.keras.layers.Dropout(0.25)(x)
#     x = tf.keras.layers.Flatten()(x)

#     x = tf.keras.layers.Dense(128, activation='relu')(x)
#     x = tf.keras.layers.Dropout(0.5)(x)

#     x = tf.keras.layers.Dense(8, activation='softmax')(x)

#     model = tf.keras.Model(img_input, x)
#     model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    
#     return model

# model = create_model()
# model.summary()

In [0]:
!pip install tf-explain

In [110]:
checkpoint = ModelCheckpoint(
    './base.model',
    monitor='val_acc',
    verbose=1,
    save_best_only=True,
    mode='max',
    save_weights_only=False,
    period=1
)
earlystop = EarlyStopping(
    monitor='val_loss',
    min_delta=0.001,
    patience=50,
    verbose=1,
    mode='auto'
)
tensorboard = TensorBoard(
    log_dir = './logs',
    histogram_freq=0,
    batch_size=16,
    write_graph=True,
    write_grads=True,
    write_images=False,
)

csvlogger = CSVLogger(
    filename= "training_csv.log",
    separator = ",",
    append = False
)

reduce = ReduceLROnPlateau(
    monitor='val_loss',
    factor=0.1,
    patience=3,
    verbose=1, 
    mode='auto'
)



/usr/local/lib/python3.6/dist-packages/keras/callbacks/tensorboard_v2.py:92: UserWarning: The TensorBoard callback `batch_size` argument (for histogram computation) is deprecated with TensorFlow 2.0. It will be ignored.
  warnings.warn('The TensorBoard callback `batch_size` argument '
/usr/local/lib/python3.6/dist-packages/keras/callbacks/tensorboard_v2.py:97: UserWarning: The TensorBoard callback does not support gradients display when using TensorFlow 2.0. The `write_grads` argument is ignored.
  warnings.warn('The TensorBoard callback does not support '


In [122]:

tup = []
# (indexes are from 0 to 7)
for ind in range(len(x_test)):
    if y_test[ind] == 1:
        tup.append(x_test[ind])
tup = np.array(tup)
print(tup.shape)

validation_array = (tup,None)
grad = tf_explain.callbacks.GradCAMCallback(
        validation_data = validation_array,
        layer_name="explain_layer",
        class_index=1
    )

callbacks = [grad]



# callbacks = [tensorboard,csvlogger,reduce]
# callbacks = [earlystop,tensorboard,csvlogger,reduce]

(7, 224, 224, 3)


In [123]:
%reload_ext tensorboard
%tensorboard --logdir logs

Reusing TensorBoard on port 6006 (pid 2741), started 0:03:58 ago. (Use '!kill 2741' to kill it.)

<IPython.core.display.Javascript object>

In [124]:


opt = SGD(lr=1e-4,momentum=0.99)
opt1 = tf.keras.optimizers.Adam(lr=1e-3)

model.compile(
    loss='categorical_crossentropy',
    optimizer=opt1,
    metrics=['accuracy']
)


# history = model.fit_generator(
#     augs_gen.flow(x_train,y_train,batch_size=32),
#     validation_data  = (x_test,y_test),
#     # steps_per_epoch=len(x_train),
#     epochs =325, 
#     verbose = 1,
#     callbacks=callbacks
# )


model.fit(x_train, y_train, batch_size=32, epochs=350, callbacks=callbacks)


Epoch 1/350
10/10 [==============================] - 2s 205ms/step - loss: 10.4054 - accuracy: 0.1100
Epoch 2/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0718 - accuracy: 0.1409
Epoch 3/350
10/10 [==============================] - 1s 72ms/step - loss: 2.1048 - accuracy: 0.1100
Epoch 4/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0832 - accuracy: 0.1409
Epoch 5/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0461 - accuracy: 0.1718
Epoch 6/350
10/10 [==============================] - 1s 71ms/step - loss: 2.0769 - accuracy: 0.1065
Epoch 7/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0770 - accuracy: 0.1753
Epoch 8/350
10/10 [==============================] - 1s 71ms/step - loss: 2.0695 - accuracy: 0.1684
Epoch 9/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0792 - accuracy: 0.1478
Epoch 10/350
10/10 [==============================] - 1s 72ms/step - loss: 2.0490 - accuracy: 0.12

/usr/local/lib/python3.6/dist-packages/tf_explain/utils/display.py:112: RuntimeWarning: invalid value encountered in true_divide
  heatmap = (heatmap - np.min(heatmap)) / (heatmap.max() - heatmap.min())


10/10 [==============================] - 1s 71ms/step - loss: 1.8122 - accuracy: 0.2715
Epoch 25/350
10/10 [==============================] - 1s 71ms/step - loss: 1.8736 - accuracy: 0.2474
Epoch 26/350
10/10 [==============================] - 1s 70ms/step - loss: 1.8855 - accuracy: 0.2612
Epoch 27/350
10/10 [==============================] - 1s 70ms/step - loss: 1.8236 - accuracy: 0.2680
Epoch 28/350
10/10 [==============================] - 1s 71ms/step - loss: 1.7694 - accuracy: 0.2784
Epoch 29/350
10/10 [==============================] - 1s 72ms/step - loss: 1.9678 - accuracy: 0.2062
Epoch 30/350
10/10 [==============================] - 1s 70ms/step - loss: 1.9316 - accuracy: 0.2474
Epoch 31/350
10/10 [==============================] - 1s 71ms/step - loss: 1.8329 - accuracy: 0.2302
Epoch 32/350
10/10 [==============================] - 1s 71ms/step - loss: 1.8333 - accuracy: 0.2440
Epoch 33/350
10/10 [==============================] - 1s 72ms/step - loss: 1.9078 - accuracy: 0.2371
Epo

In [0]:
show_final_history(history)
# model.load_weights('./base.model')

# model_json = model.to_json()
# with open("model.json","w") as json_file:
#     json_file.write(model_json)
    
# model.save("model.h5")
# print("Weights Saved")